In [2]:
import requests,json
from bs4 import BeautifulSoup
from selenium import webdriver
from webdriver_manager.chrome import ChromeDriverManager

user_agent='Mozilla/5.0 (Macintosh; Intel Mac OS X 11_3_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36'
path = '/Users/williamlee/Desktop/Work/Changing_room/chromedriver'
options = webdriver.ChromeOptions()
options.add_argument('--ignore-certificate-errors')
options.add_argument('--incognito')
options.add_argument('--headless')
options.add_argument("--window-size=1920,1080")
options.add_argument('--ignore-certificate-errors')
options.add_argument('--allow-running-insecure-content')
options.add_argument(f'user-agent={user_agent}')
driver = webdriver.Chrome(executable_path=ChromeDriverManager().install(), options=options)#use the chromedirver, change it to your own path

import time

[WDM] - Current google-chrome version is 95.0.4638
[WDM] - Get LATEST driver version for 95.0.4638


[WDM] - There is no [mac64] chromedriver for browser 95.0.4638 in cache
[WDM] - Get LATEST driver version for 95.0.4638
[WDM] - Trying to download new driver from http://chromedriver.storage.googleapis.com/95.0.4638.54/chromedriver_mac64.zip
[WDM] - Driver has been saved in cache [/Users/sarahamiraslani/.wdm/drivers/chromedriver/mac64/95.0.4638.54]


In [3]:
from tqdm import tqdm
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import json
import requests
import re
import itertools
import csv

In [4]:
#headers={'User-Agent':'Mozilla/5.0 (Windows NT 10.0; Win64; x64)'\ 'AppleWebKit/537.36 (KHTML, like Gecko)'\ 'Chrome/84.0.4147.135 Safari/537.36'}
headers={'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) '\
           'AppleWebKit/537.36 (KHTML, like Gecko) '\
           'Chrome/75.0.3770.80 Safari/537.36'}

<h4>Get the women links<h4>

In [7]:
#url=("https://www2.hm.com/en_asia5/index.html")
#url='https://www2.hm.com/en_asia5/ladies/shop-by-product/view-all.html'
#url='https://www2.hm.com/en_us/women/products/view-all.html'
#url='https://www2.hm.com/en_us/men/products/view-all.html?offset=900&page-size=36'
url='https://www2.hm.com/en_us/women/products/view-all.html?offset=5436&page-size=36'
import time
import concurrent.futures
response=requests.get(url,headers=headers)
results_page = BeautifulSoup(response.content.decode('utf-8'),'lxml') 

start_time = time.time()
view_all_links=['https://www2.hm.com/en_us/women/products/view-all.html']
while results_page.find_all('a',class_='pagination-links-list'):
    link=results_page.find('a',class_='pagination-links-list').get('href')
    view_all_links.append(link)
    time.sleep(2)
    response=requests.get(link,headers=headers)
    with concurrent.futures.ThreadPoolExecutor(max_workers = 10) as executor:
        executor.map(s)
    results_page = BeautifulSoup(response.content.decode('utf-8'),'lxml') 

In [8]:
view_all_links

['https://www2.hm.com/en_us/women/products/view-all.html']

<h4>Get item<h4>

In [41]:
final_result={}
prelink='https://www2.hm.com'
name=[]
links=[]
for i in view_all_links:
    response=requests.get(i,headers=headers)
    results_page = BeautifulSoup(response.content.decode('utf-8'),'lxml') 
    items=results_page.find_all('a',class_='item-link')
    for j in items:
        time.sleep(0.5)
        link=prelink+j.get('href')
        #if j.get('title') not in final_result.keys():
            #final_result[j.get('title')]=link
        name.append(j.get('title'))
        links.append(link)
        

In [43]:
len(name)

5220

<h4>Store the temp data for future use<h4>

In [20]:
import csv
with open('hm_men_link.csv', 'w',encoding='utf-8') as csv_file:  
    writer = csv.writer(csv_file)
    for key, value in final_result.items():
       writer.writerow([key, value])

In [45]:
import csv
with open('dict.csv', mode='r') as infile:
    reader = csv.reader(infile)
    final_result = {rows[0]:rows[1] for rows in reader if rows!=[]}

<h4>Get the material and the image link<h4>

In [44]:
result_material={}
result_image={}
#hm_result={}
hm=[]

'''hm_result['Name']=[]
hm_result['Material']=[]
hm_result['Color']=[]
hm_result['URL']=[]
hm_result['Image']=[]
hm_result['Brand_name']=[]
hm_result['High_level_shape']=[]
hm_result['Price']=[]
hm_result['Size']=[]
'''

#for k,w in final_result.items():
for num in range(len(name)):
    hm_result={}
   
    time.sleep(0.5)
    response=requests.get(links[num],headers=headers)
    results_page = BeautifulSoup(response.content.decode('utf-8'),'lxml') 
    dl=results_page.find_all('dl',class_='pdp-description-list')
    try:
        image=results_page.find('div',class_='product-detail-main-image-container').find('img').get('src')
    except:
        continue
    #result_material[k]=[]
    #result_image[k]=image
    
    
    temp=[]
    for i in dl:
        try:
            li=i.find_all('li')
            for j in li:
                temp.append(j.get_text())
                #result_material[k].append(j.get_text())
        except:
            pass
    
    #color
    prep_color=results_page.find('div',class_='mini-slider')
    colors=prep_color.find_all('li',class_='list-item')
    color=[]
    for i in colors:
        color.append(i.find('a').get('data-color'))
     
    #price
    price=results_page.find('span',class_='price-value').get_text().replace('\n', '').replace('\r', '').replace(' ','')
    
    #size
    driver.get(links[num])
    more_buttons=driver.find_elements_by_class_name("picker small-picker item loaded")
    for x in range(len(more_buttons)):
            if more_buttons[x].is_displayed():
                driver.execute_script("arguments[0].click();", more_buttons[x])
                time.sleep(0.1)
    page_source = driver.page_source
    soup = BeautifulSoup(page_source, 'lxml')
    sizes=soup.find_all('span',class_='value')
    size=set()
    for i in sizes:
        t=i.get_text().replace('\n', '').replace('\r', '').replace(' ','').replace('\t','')
        if t!='Selectsize' and t!='Outofstock':
        #if i.get_text()!='\n\t\t    Select size' and i.get_text()!='Select size' and i.get_text()!='Out of stock' and len(i.get_text())<8:
            size.add(t)
            
#'Name', 'Material', 'Color', 'URL', 'Image','Brand_name','High_level_shape','Price','Size    
    hm_result['Name']=name[num]
    hm_result['Material']=temp
    hm_result['Color']=color
    hm_result['URL']=links[num]
    hm_result['Image']=image
    hm_result['Brand_name']='HM'
    
    #high level shape
    shape=results_page.find('ul',class_='breadcrumbs-list')
    level_shape=shape.find_all('li',class_='breadcrumb-list-item')
    level_result=[]
    for i in level_shape:
        level_result.append(i.find('span').get_text())
    if len(level_result)<=2:
        hm_result['High_level_shape']=level_result[1]
    else:
        hm_result['High_level_shape']=level_result[2]
    
    hm_result['Price']=price
    hm_result['Season']=''
    hm_result['Size']=(list(size)) 
    hm_result['Formality']=''
    hm_result['Description']=results_page.find('p',class_='pdp-description-text').get_text()
    
    
    hm.append(hm_result)
    


In [47]:
len(hm)

5218

<h4>Write into csv file<h4>

In [46]:
import csv
with open("hm_women.csv",'w',encoding='utf-8') as f:
   # Using dictionary keys as fieldnames for the CSV file header
   writer = csv.DictWriter(f, hm[0].keys())
   writer.writeheader()
   for d in hm:
      writer.writerow(d)

In [14]:
df = pd.read_csv('hm_zara_table.csv', encoding="cp1252")

In [9]:
import chardet    
rawdata = open('hm_zara_table.csv', 'rb').read()
result = chardet.detect(rawdata)
charenc = result['encoding']
print(charenc)

Windows-1252


### h&m rescraping

In [2]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import TimeoutException, StaleElementReferenceException, NoSuchElementException
from bs4 import BeautifulSoup
from tqdm import tqdm
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import json
import requests
import re
import itertools
import time
import threading
import concurrent.futures
import csv
import random

In [3]:
# get that from the sitemap
def get_link(url):
    HEADERS = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36'}
    content = requests.get(url, headers=HEADERS)
    soup = BeautifulSoup(content.text, 'html.parser')
    loc = soup.find_all('loc')
    loc = [i.get_text() for i in loc if 'product' in i.get_text()]
    return loc

In [4]:
url = 'https://www2.hm.com/en_us.sitemap.xml'
all_link = get_link(url)

In [5]:
product_link = []
def get_product(url):
    HEADERS = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36'}
    content = requests.get(url, headers=HEADERS)
    soup = BeautifulSoup(content.text, 'html.parser')
    loc = soup.find_all('loc')
    loc = [i.get_text() for i in loc]
    return loc

In [6]:
for i in all_link:
    product_link += get_product(i)
product_link = list(set(product_link))
len(product_link)

14908

In [7]:
import extruct
from w3lib.html import get_base_url
HEADERS = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36'}
def get_metadata(html: bytes, url: str):
    """Fetch JSON-LD structured data."""
    all_meta = extruct.extract(
        html,
        base_url = get_base_url(url),
        syntaxes = ['json-ld'],
        uniform = True
    )
    metadata = all_meta['json-ld']
    if bool(metadata) and isinstance(metadata, list):
        metadata = metadata[0]
    return metadata

In [131]:
hm_df = pd.DataFrame(columns=['Name', 'Material', 'Color', 'Size', 'Price', 'URL', 'Image', 'Brand_name', 'Description'])
def get_detail(url_list):    
    global hm_df
    for url in tqdm(url_list):
        product_dict = {}
        user_agent_list = [
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 11_3_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.97 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/32.0.1664.3 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_3) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/27.0.1453.93 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_7_2) AppleWebKit/535.24 (KHTML, like Gecko) Chrome/19.0.1055.1 Safari/535.24'
        ]
        user_agent = user_agent_list[random.randint(0,5)]
        HEADERS = {'User-Agent': user_agent_list[random.randint(0,5)]}
        path = '/Users/williamlee/Desktop/Work/Changing_room/chromedriver'
        options = webdriver.ChromeOptions()
        options.add_argument('--headless')
        options.add_argument("--window-size=1920,1080")
        options.add_argument('--ignore-certificate-errors')
        options.add_argument('--allow-running-insecure-content')
        options.add_argument(f'user-agent={user_agent}')
        driver = webdriver.Chrome(executable_path=path, options=options)
        driver.get(url)
        try:
#             name = driver.find_element_by_tag_name('h1')
#             product_dict['Name'] = name.text

            material = driver.find_element_by_xpath("//div[@class='pdp-description-list-item']//dd//ul")
            product_dict['Material'] = material.text

#             color = driver.find_element_by_tag_name('h3')
#             product_dict['Color'] = [color.text]
            
#             time.sleep(0.8)
            
            button = driver.find_element_by_xpath("//div[@class='product-item-buttons']//div[@class='product-button-wrapper']//div[@class='picker small-picker item loaded']//button[@type='button']")
            button.click()
            perf_match = re.compile("option $")
            elems = driver.find_elements_by_xpath("//div[@class='picker-option']//button[@class='option ']")
            sub = ['size', 'notify']
            sizes = [elem.text for elem in elems if 'size' not in elem.text]
            product_dict['Size'] = sizes

#             price = driver.find_element_by_xpath("//div[@class='ProductPrice-module--productItemPrice__2rpyB']")
#             product_dict['Price'] = price.text

            product_dict['URL'] = url

#             image = driver.find_element_by_xpath("//div[@class='product-detail-main-image-container']//img").get_attribute('src')
#             product_dict['Image'] = {color.text: image}

            product_dict['Brand_name'] = 'hm'

#             description = driver.find_element_by_xpath("//p[@class='pdp-description-text']")
#             product_dict['Description'] = description.get_attribute("textContent")
            
            metadata = get_metadata(requests.get(url, headers = HEADERS).text, url)
            product_dict['Name'] = metadata['name']
            product_dict['Color'] = [metadata['color']]
            product_dict['Price'] = '$ ' + metadata['price']
            product_dict['Image'] = {metadata['color']: 'https:' + metadata['image']}
            product_dict['Description'] = metadata['description']
            
            
            driver.quit()

        except (NoSuchElementException, AttributeError, TypeError):
            driver.quit()
            continue
             
#     metadata = get_metadata(requests.get(url, headers = HEADERS).text, url)
#     product_dict['Name'] = metadata['name']
#     product_dict['Color'] = [metadata['color']]
#     product_dict['Image'] = {metadata['color']: 'https:' + metadata['image']}
#     product_dict['Description'] = metadata['description']
        
        hm_df = hm_df.append(product_dict, ignore_index=True)

In [250]:
# hm_df_2 = pd.DataFrame(columns=['Name', 'Material', 'Color', 'Size', 'Price', 'URL', 'Image', 'Brand_name', 'Description'])
def get_detail_clean(url_list):    
    global hm_df_2
    for url in tqdm(url_list):
        product_dict = {}
        user_agent_list = [
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 11_3_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.97 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/32.0.1664.3 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_3) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/27.0.1453.93 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_7_2) AppleWebKit/535.24 (KHTML, like Gecko) Chrome/19.0.1055.1 Safari/535.24',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_6_6) AppleWebKit/534.24 (KHTML, like Gecko) Chrome/11.0.698.0 Safari/534.24',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_3) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/54.0.2866.71 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_9_2) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/52.0.2762.73 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_4) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/49.0.2656.18 Safari/537.36'
        ]
        user_agent = user_agent_list[random.randint(0,9)]
        HEADERS = {'User-Agent': user_agent_list[random.randint(0,9)]}
        path = '/Users/williamlee/Desktop/Work/Changing_room/chromedriver'
        options = webdriver.ChromeOptions()
        options.add_argument('--headless')
        options.add_argument("--window-size=1920,1080")
        options.add_argument('--ignore-certificate-errors')
        options.add_argument('--allow-running-insecure-content')
        options.add_argument(f'user-agent={user_agent}')
        driver = webdriver.Chrome(executable_path=path, options=options)
        driver.get(url)
        try:
            material = driver.find_element_by_xpath("//div[@class='pdp-description-list-item']//dt[text() = 'Composition']/following::*/*")
            product_dict['Material'] = material.text
            
            button = driver.find_element_by_xpath("//div[@class='product-item-buttons']//div[@class='product-button-wrapper']//div[@class='picker small-picker item loaded']//button[@type='button']")
            button.click()
            perf_match = re.compile("option $")
            elems = driver.find_elements_by_xpath("//div[@class='picker-option']//button[@class='option ']")
            sub = ['size', 'notify']
            sizes = [elem.text for elem in elems if 'size' not in elem.text]
            product_dict['Size'] = sizes

            product_dict['URL'] = url
            product_dict['Brand_name'] = 'hm'

            metadata = get_metadata(requests.get(url, headers = HEADERS).text, url)
            product_dict['Name'] = metadata['name']
            product_dict['Color'] = [metadata['color']]
            product_dict['Price'] = '$ ' + metadata['offers'][0]['price']
            product_dict['Image'] = {metadata['color']: 'https:' + metadata['image']}
            product_dict['Description'] = metadata['description']
                
            driver.quit()

        except (NoSuchElementException, AttributeError, TypeError):
            driver.quit()
            continue
        
        hm_df_2 = hm_df_2.append(product_dict, ignore_index=True)

In [261]:
url = product_link[14211:]
get_detail_clean(url)
















































  0%|          | 0/697 [00:00<?, ?it/s]














































  0%|          | 1/697 [00:05<1:02:00,  5.35s/it]














































  0%|          | 2/697 [00:10<1:00:21,  5.21s/it]














































  0%|          | 3/697 [00:20<1:16:53,  6.65s/it]














































  1%|          | 4/697 [00:25<1:10:32,  6.11s/it]














































  1%|          | 5/697 [00:29<1:04:39,  5.61s/it]














































  1%|          | 6/697 [00:34<1:01:32,  5.34s/it]














































  1%|          | 7/697 [00:39<59:41,  5.19s/it]  














































  1%|          | 8/697 [00:43<58:02,  5.06s/it]














































  1%|▏         | 9/697 [00:48<56:51,  4.96s/it]














































  1%|▏ 

  5%|▍         | 34/697 [02:39<46:37,  4.22s/it]














































  5%|▌         | 35/697 [02:43<46:21,  4.20s/it]














































  5%|▌         | 36/697 [02:47<46:56,  4.26s/it]














































  5%|▌         | 37/697 [02:52<48:38,  4.42s/it]














































  5%|▌         | 38/697 [02:57<49:46,  4.53s/it]














































  6%|▌         | 39/697 [03:02<50:58,  4.65s/it]














































  6%|▌         | 40/697 [03:07<51:47,  4.73s/it]














































  6%|▌         | 41/697 [03:11<50:38,  4.63s/it]














































  6%|▌         | 42/697 [03:15<49:23,  4.53s/it]














































  6%|▌         | 43/697 [03:20<49:50,  4.57s/it]














































  6%|▋         | 44/697 [03:25<49:55,  4.59s/it]



 10%|▉         | 68/697 [05:08<44:31,  4.25s/it]














































 10%|▉         | 69/697 [05:13<44:17,  4.23s/it]














































 10%|█         | 70/697 [05:17<43:41,  4.18s/it]














































 10%|█         | 71/697 [05:21<43:49,  4.20s/it]














































 10%|█         | 72/697 [05:25<43:57,  4.22s/it]














































 10%|█         | 73/697 [05:29<41:59,  4.04s/it]














































 11%|█         | 74/697 [05:33<42:29,  4.09s/it]














































 11%|█         | 75/697 [05:37<42:31,  4.10s/it]














































 11%|█         | 76/697 [05:41<42:41,  4.13s/it]














































 11%|█         | 77/697 [05:45<42:29,  4.11s/it]














































 11%|█         | 78/697 [05:49<42:31,  4.12s/it]



 15%|█▍        | 102/697 [07:33<42:51,  4.32s/it]














































 15%|█▍        | 103/697 [07:38<44:27,  4.49s/it]














































 15%|█▍        | 104/697 [07:41<40:59,  4.15s/it]














































 15%|█▌        | 105/697 [07:45<41:55,  4.25s/it]














































 15%|█▌        | 106/697 [07:50<42:47,  4.34s/it]














































 15%|█▌        | 107/697 [07:54<42:39,  4.34s/it]














































 15%|█▌        | 108/697 [07:59<43:00,  4.38s/it]














































 16%|█▌        | 109/697 [08:03<43:33,  4.44s/it]














































 16%|█▌        | 110/697 [08:08<44:09,  4.51s/it]














































 16%|█▌        | 111/697 [08:13<44:26,  4.55s/it]














































 16%|█▌        | 112/697 [08:17<44:04,  

 20%|█▉        | 136/697 [10:06<40:59,  4.38s/it]














































 20%|█▉        | 137/697 [10:10<40:11,  4.31s/it]














































 20%|█▉        | 138/697 [10:14<39:48,  4.27s/it]














































 20%|█▉        | 139/697 [10:19<39:20,  4.23s/it]














































 20%|██        | 140/697 [10:23<39:46,  4.28s/it]














































 20%|██        | 141/697 [10:27<40:12,  4.34s/it]














































 20%|██        | 142/697 [10:32<40:15,  4.35s/it]














































 21%|██        | 143/697 [10:36<40:26,  4.38s/it]














































 21%|██        | 144/697 [10:40<39:54,  4.33s/it]














































 21%|██        | 145/697 [10:45<39:48,  4.33s/it]














































 21%|██        | 146/697 [10:49<39:15,  

...

 78%|███████▊  | 544/697 [40:01<11:57,  4.69s/it]














































 78%|███████▊  | 545/697 [40:06<11:41,  4.61s/it]














































 78%|███████▊  | 546/697 [40:10<11:40,  4.64s/it]














































 78%|███████▊  | 547/697 [40:16<12:06,  4.84s/it]














































 79%|███████▊  | 548/697 [40:20<11:33,  4.66s/it]














































 79%|███████▉  | 549/697 [40:24<10:57,  4.44s/it]














































 79%|███████▉  | 550/697 [40:28<11:00,  4.49s/it]














































 79%|███████▉  | 551/697 [40:33<10:49,  4.45s/it]














































 79%|███████▉  | 552/697 [40:37<10:22,  4.29s/it]














































 79%|███████▉  | 553/697 [40:41<10:19,  4.30s/it]














































 79%|███████▉  | 554/697 [40:45<10:17,  

 83%|████████▎ | 578/697 [42:33<08:35,  4.33s/it]














































 83%|████████▎ | 579/697 [42:37<08:31,  4.34s/it]














































 83%|████████▎ | 580/697 [42:41<08:22,  4.29s/it]














































 83%|████████▎ | 581/697 [42:46<08:13,  4.25s/it]














































 84%|████████▎ | 582/697 [42:50<08:03,  4.20s/it]














































 84%|████████▎ | 583/697 [42:54<08:01,  4.22s/it]














































 84%|████████▍ | 584/697 [42:58<07:55,  4.21s/it]














































 84%|████████▍ | 585/697 [43:02<07:56,  4.25s/it]














































 84%|████████▍ | 586/697 [43:07<08:01,  4.34s/it]














































 84%|████████▍ | 587/697 [43:11<07:54,  4.31s/it]














































 84%|████████▍ | 588/697 [43:15<07:30,  

 88%|████████▊ | 612/697 [44:58<06:03,  4.27s/it]














































 88%|████████▊ | 613/697 [45:03<06:00,  4.29s/it]














































 88%|████████▊ | 614/697 [45:06<05:29,  3.97s/it]














































 88%|████████▊ | 615/697 [45:10<05:34,  4.08s/it]














































 88%|████████▊ | 616/697 [45:15<05:51,  4.33s/it]














































 89%|████████▊ | 617/697 [45:20<05:56,  4.46s/it]














































 89%|████████▊ | 618/697 [45:24<05:49,  4.43s/it]














































 89%|████████▉ | 619/697 [45:28<05:40,  4.37s/it]














































 89%|████████▉ | 620/697 [45:33<05:38,  4.40s/it]














































 89%|████████▉ | 621/697 [45:38<05:39,  4.47s/it]














































 89%|████████▉ | 622/697 [45:42<05:31,  

 93%|█████████▎| 646/697 [47:29<03:41,  4.34s/it]














































 93%|█████████▎| 647/697 [47:33<03:39,  4.39s/it]














































 93%|█████████▎| 648/697 [47:37<03:27,  4.24s/it]














































 93%|█████████▎| 649/697 [47:42<03:26,  4.31s/it]














































 93%|█████████▎| 650/697 [47:46<03:25,  4.38s/it]














































 93%|█████████▎| 651/697 [47:51<03:21,  4.37s/it]














































 94%|█████████▎| 652/697 [47:54<03:09,  4.21s/it]














































 94%|█████████▎| 653/697 [47:59<03:10,  4.33s/it]














































 94%|█████████▍| 654/697 [48:03<02:59,  4.18s/it]














































 94%|█████████▍| 655/697 [48:07<03:00,  4.29s/it]














































 94%|█████████▍| 656/697 [48:12<02:56,  

 98%|█████████▊| 680/697 [50:02<01:19,  4.66s/it]














































 98%|█████████▊| 681/697 [50:06<01:13,  4.57s/it]














































 98%|█████████▊| 682/697 [50:11<01:08,  4.55s/it]














































 98%|█████████▊| 683/697 [50:16<01:07,  4.81s/it]














































 98%|█████████▊| 684/697 [50:21<01:01,  4.74s/it]














































 98%|█████████▊| 685/697 [50:25<00:56,  4.72s/it]














































 98%|█████████▊| 686/697 [50:30<00:51,  4.67s/it]














































 99%|█████████▊| 687/697 [50:34<00:45,  4.58s/it]














































 99%|█████████▊| 688/697 [50:39<00:40,  4.54s/it]














































 99%|█████████▉| 689/697 [50:43<00:36,  4.57s/it]














































 99%|█████████▉| 690/697 [50:48<00:32,  

In [263]:
hm_df_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 14505 entries, 0 to 14504
Data columns (total 9 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   Name         14505 non-null  object
 1   Material     14505 non-null  object
 2   Color        14505 non-null  object
 3   Size         14505 non-null  object
 4   Price        14505 non-null  object
 5   URL          14505 non-null  object
 6   Image        14505 non-null  object
 7   Brand_name   14505 non-null  object
 8   Description  14505 non-null  object
dtypes: object(9)
memory usage: 1020.0+ KB


In [264]:
hm_df_2.to_csv('hm_version1.csv', index=False)

In [283]:
def check_material(cell):
    if '%' not in cell['Material']:
        user_agent_list = [
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 11_3_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/90.0.4430.93 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_5) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/83.0.4103.97 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_6) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/87.0.4280.141 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/32.0.1664.3 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_3) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/27.0.1453.93 Safari/537.36',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_7_2) AppleWebKit/535.24 (KHTML, like Gecko) Chrome/19.0.1055.1 Safari/535.24',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_6_6) AppleWebKit/534.24 (KHTML, like Gecko) Chrome/11.0.698.0 Safari/534.24',
        'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_8_3) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/54.0.2866.71 Safari/537.36'
        ]
        user_agent = user_agent_list[random.randint(0,7)]
        HEADERS = {'User-Agent': user_agent_list[random.randint(0,7)]}
        path = '/Users/williamlee/Desktop/Work/Changing_room/chromedriver'
        options = webdriver.ChromeOptions()
        options.add_argument('--headless')
        options.add_argument("--window-size=1920,1080")
        options.add_argument('--ignore-certificate-errors')
        options.add_argument('--allow-running-insecure-content')
        options.add_argument(f'user-agent={user_agent}')
        driver = webdriver.Chrome(executable_path=path, options=options)
        driver.get(cell['URL'])
        try:
            material = driver.find_element_by_xpath("//div[@class='pdp-description-list-item']//dt[text() = 'Composition']/following::*/*").text
            driver.quit()
            return material

        except (NoSuchElementException, AttributeError, TypeError):
            driver.quit()
            return cell['Material']
    else:
        return cell['Material']

In [300]:
hm_df_4 = hm_df_2.copy()
hm_df_4['Material_Clean'].iloc[10000:] = hm_df_4.iloc[10000:].apply(check_material, axis=1)

In [390]:
hm_df_5 = hm_df_4.copy()
hm_df_5.drop('Material', axis=1, inplace=True)
hm_df_5.rename(columns={'Material_Clean': 'Material'}, inplace=True)

In [393]:
def size_clean(cell):
    if cell['Size'] == []:
        return ['']
    else:
        output = []
        a = ''
        for i in cell['Size']:
            a = i.replace('\nNotify me', '')
            a = a.replace('\nFew pieces left', '')
            output.append(a)
        return output
        
hm_df_5['Size_Clean'] = hm_df_5.apply(size_clean, axis=1)

In [394]:
hm_df_6 = hm_df_5.copy()
hm_df_6.drop('Size', axis=1, inplace=True)
hm_df_6.rename(columns={'Size_Clean': 'Size'}, inplace=True)

In [395]:
# hm_df_6.to_csv('hm_version2.csv', index=False)

In [413]:
def color_clean(cell):
    if cell['Color'] == []:
        return ['']
    else:
        return cell['Color']
hm_df_6['Color_Clean'] = hm_df_6.apply(color_clean, axis=1)
hm_df_6.drop('Color', axis=1, inplace=True)
hm_df_6.rename(columns={'Color_Clean': 'Color'}, inplace=True)

In [436]:
hm_df_3 = pd.DataFrame(columns=['Name', 'Material', 'Color', 'Size', 'Price', 'URL', 'Image', 'Brand_name', 'Description'])
def create_new(df):
    global hm_df_3
    for j in tqdm(range(len(df))):
        flag = 0
        for i in range(len(hm_df_3)):
            if df['Description'].iloc[j] == hm_df_3['Description'].iloc[i]:
                color = df['Color'].iloc[j][0]
                hm_df_3['Image'].iloc[i][color] = df['Image'].iloc[j].get(color)
                hm_df_3['Color'].iloc[i].append(color)
                flag = 1
        if flag == 0:
            hm_df_3 = hm_df_3.append(df.iloc[j], ignore_index=True)

In [439]:
create_new(hm_df_6)
















































  0%|          | 0/14505 [00:00<?, ?it/s]














































  0%|          | 26/14505 [00:00<00:57, 252.85it/s]














































  0%|          | 51/14505 [00:00<00:57, 250.40it/s]














































  1%|          | 75/14505 [00:00<00:58, 246.71it/s]














































  1%|          | 97/14505 [00:00<01:01, 235.72it/s]














































  1%|          | 118/14505 [00:00<01:04, 224.41it/s]














































  1%|          | 137/14505 [00:00<01:10, 203.73it/s]














































  1%|          | 155/14505 [00:00<01:19, 180.42it/s]














































  1%|          | 172/14505 [00:00<01:23, 171.57it/s]














































  1%|▏         | 189/14505 [00:00<01:26, 166.25it/s]


























  3%|▎         | 503/14505 [00:03<02:39, 87.82it/s]














































  4%|▎         | 512/14505 [00:03<02:38, 88.25it/s]














































  4%|▎         | 521/14505 [00:04<02:39, 87.46it/s]














































  4%|▎         | 530/14505 [00:04<03:03, 75.96it/s]














































  4%|▎         | 538/14505 [00:04<03:01, 76.89it/s]














































  4%|▍         | 546/14505 [00:04<03:02, 76.63it/s]














































  4%|▍         | 555/14505 [00:04<02:57, 78.46it/s]














































  4%|▍         | 563/14505 [00:04<03:01, 76.87it/s]














































  4%|▍         | 571/14505 [00:04<03:01, 76.60it/s]














































  4%|▍         | 580/14505 [00:04<02:55, 79.22it/s]














































  4%|▍         | 588

  5%|▌         | 768/14505 [00:07<03:45, 60.98it/s]














































  5%|▌         | 775/14505 [00:07<03:44, 61.11it/s]














































  5%|▌         | 782/14505 [00:07<03:40, 62.26it/s]














































  5%|▌         | 789/14505 [00:07<03:39, 62.42it/s]














































  5%|▌         | 796/14505 [00:08<03:39, 62.53it/s]














































  6%|▌         | 803/14505 [00:08<03:36, 63.39it/s]














































  6%|▌         | 810/14505 [00:08<03:36, 63.33it/s]














































  6%|▌         | 817/14505 [00:08<03:39, 62.39it/s]














































  6%|▌         | 824/14505 [00:08<03:44, 60.91it/s]














































  6%|▌         | 831/14505 [00:08<03:39, 62.37it/s]














































  6%|▌         | 838

  7%|▋         | 989/14505 [00:11<04:12, 53.54it/s]














































  7%|▋         | 995/14505 [00:11<04:09, 54.10it/s]














































  7%|▋         | 1001/14505 [00:11<04:08, 54.33it/s]














































  7%|▋         | 1007/14505 [00:11<04:08, 54.21it/s]














































  7%|▋         | 1013/14505 [00:11<04:08, 54.30it/s]














































  7%|▋         | 1019/14505 [00:11<04:10, 53.89it/s]














































  7%|▋         | 1025/14505 [00:12<04:12, 53.44it/s]














































  7%|▋         | 1031/14505 [00:12<04:18, 52.09it/s]














































  7%|▋         | 1037/14505 [00:12<04:22, 51.31it/s]














































  7%|▋         | 1043/14505 [00:12<04:26, 50.49it/s]














































  7%|▋      

  8%|▊         | 1172/14505 [00:15<04:35, 48.44it/s]














































  8%|▊         | 1177/14505 [00:15<04:37, 47.95it/s]














































  8%|▊         | 1183/14505 [00:15<04:33, 48.76it/s]














































  8%|▊         | 1188/14505 [00:15<04:37, 48.02it/s]














































  8%|▊         | 1193/14505 [00:15<04:40, 47.41it/s]














































  8%|▊         | 1198/14505 [00:15<04:37, 48.02it/s]














































  8%|▊         | 1203/14505 [00:15<04:39, 47.51it/s]














































  8%|▊         | 1208/14505 [00:15<04:42, 47.15it/s]














































  8%|▊         | 1213/14505 [00:16<04:45, 46.62it/s]














































  8%|▊         | 1218/14505 [00:16<04:58, 44.56it/s]














































  8%|▊    

...

 99%|█████████▉| 14366/14505 [18:02<00:17,  7.95it/s]














































 99%|█████████▉| 14367/14505 [18:02<00:17,  7.97it/s]














































 99%|█████████▉| 14368/14505 [18:03<00:17,  8.00it/s]














































 99%|█████████▉| 14369/14505 [18:03<00:16,  8.03it/s]














































 99%|█████████▉| 14370/14505 [18:03<00:17,  7.92it/s]














































 99%|█████████▉| 14371/14505 [18:03<00:16,  7.99it/s]














































 99%|█████████▉| 14372/14505 [18:03<00:16,  8.02it/s]














































 99%|█████████▉| 14373/14505 [18:03<00:16,  7.95it/s]














































 99%|█████████▉| 14374/14505 [18:03<00:16,  7.98it/s]














































 99%|█████████▉| 14375/14505 [18:03<00:16,  7.95it/s]
















































 99%|█████████▉| 14400/14505 [18:07<00:13,  7.94it/s]














































 99%|█████████▉| 14401/14505 [18:07<00:13,  7.99it/s]














































 99%|█████████▉| 14402/14505 [18:07<00:12,  8.01it/s]














































 99%|█████████▉| 14403/14505 [18:07<00:13,  7.40it/s]














































 99%|█████████▉| 14404/14505 [18:07<00:13,  7.53it/s]














































 99%|█████████▉| 14405/14505 [18:07<00:13,  7.64it/s]














































 99%|█████████▉| 14406/14505 [18:07<00:12,  7.72it/s]














































 99%|█████████▉| 14407/14505 [18:08<00:12,  7.85it/s]














































 99%|█████████▉| 14408/14505 [18:08<00:12,  7.93it/s]














































 99%|█████████▉| 14409/14505 [18:08<00:12,  7.97it/s]
















































100%|█████████▉| 14434/14505 [18:11<00:09,  7.70it/s]














































100%|█████████▉| 14435/14505 [18:11<00:09,  7.75it/s]














































100%|█████████▉| 14436/14505 [18:11<00:08,  7.82it/s]














































100%|█████████▉| 14437/14505 [18:11<00:08,  7.92it/s]














































100%|█████████▉| 14438/14505 [18:11<00:08,  7.94it/s]














































100%|█████████▉| 14439/14505 [18:12<00:08,  7.91it/s]














































100%|█████████▉| 14440/14505 [18:12<00:08,  7.88it/s]














































100%|█████████▉| 14441/14505 [18:12<00:08,  7.94it/s]














































100%|█████████▉| 14442/14505 [18:12<00:07,  7.92it/s]














































100%|█████████▉| 14443/14505 [18:12<00:07,  7.87it/s]
















































100%|█████████▉| 14468/14505 [18:15<00:04,  8.02it/s]














































100%|█████████▉| 14469/14505 [18:15<00:04,  8.03it/s]














































100%|█████████▉| 14470/14505 [18:15<00:04,  8.07it/s]














































100%|█████████▉| 14471/14505 [18:16<00:04,  8.04it/s]














































100%|█████████▉| 14472/14505 [18:16<00:04,  8.05it/s]














































100%|█████████▉| 14473/14505 [18:16<00:03,  8.06it/s]














































100%|█████████▉| 14474/14505 [18:16<00:03,  8.08it/s]














































100%|█████████▉| 14475/14505 [18:16<00:03,  8.09it/s]














































100%|█████████▉| 14476/14505 [18:16<00:03,  8.07it/s]














































100%|█████████▉| 14477/14505 [18:16<00:03,  8.08it/s]
















































100%|█████████▉| 14502/14505 [18:19<00:00,  7.97it/s]














































100%|█████████▉| 14503/14505 [18:20<00:00,  7.97it/s]














































100%|█████████▉| 14504/14505 [18:20<00:00,  7.92it/s]














































100%|██████████| 14505/14505 [18:20<00:00, 13.18it/s]


In [443]:
count = 0
for i in hm_df_3.Image:
    if len(i.keys()) >= 2:
        count+=1
print(count)

3291


In [453]:
# hm_df_3.to_csv('hm_final.csv', index=False)

In [368]:
product_link_test = product_link[:20]
start_time = time.time()

for url in product_link_test:
    product_dict = get_detail(url)
    flag = 0
    for i in range(len(hm_df)):
        if product_dict['Description'] == hm_df['Description'].iloc[i]:
            hm_df['Image'].iloc[i][product_dict['Color'][0]] = product_dict['Image'].get(product_dict['Color'][0])
            hm_df['Color'].iloc[i].append(product_dict['Color'][0])
            flag = 1
    if flag == 0:
        hm_df = hm_df.append(product_dict, ignore_index=True)
    
end_time = time.time()

print(end_time - start_time)


115.88122415542603


In [33]:
product_link_test = product_link[50:100]
start_time = time.time()

with concurrent.futures.ThreadPoolExecutor(max_workers = 6) as executor:
    result_futures = list(map(lambda x: executor.submit(get_detail, x), product_link_test))
    results = [f.result() for f in concurrent.futures.as_completed(result_futures)]
    for product_dict in results:
        flag = 0
        for i in range(len(hm_df)):
            if product_dict['Description'] == hm_df['Description'].iloc[i]:
                hm_df['Image'].iloc[i][product_dict['Color'][0]] = product_dict['Image'].get(product_dict['Color'][0])
                hm_df['Color'].iloc[i].append(product_dict['Color'][0])
                flag = 1
                break
        if flag == 0:
            hm_df = hm_df.append(product_dict, ignore_index=True)
    
end_time = time.time()

print(end_time - start_time)

NoSuchElementException: Message: no such element: Unable to locate element: {"method":"xpath","selector":"//div[@class='pdp-description-list-item']//dd//ul"}
  (Session info: headless chrome=90.0.4430.212)


In [34]:
hm_df

Name  \
0   iPhone Case and AirPods Case   
1                Printed T-shirt   
2   2-pack Linen-blend Placemats   
3                    Short Dress   
4                  MAMA Leggings   
5           3-pack Jersey Shirts   
6              Modal Twill Pants   
7      MAMA Cotton Nursing Dress   
8   Tank Top with Printed Design   
9               Pendant Necklace   
10                   Nail polish   
11                       Joggers   
12            Color-block Hoodie   
13         Water-repellent Parka   
14         3-pack Cotton Pajamas   
15                Bikini Bottoms   
16                  Sports Shirt   
17                 Creased Pants   
18   3-pack Flutter-sleeved Tops   
19     MAMA Ruffle-trimmed Dress   
20               Boxy Sweatshirt   
21             MAMA Cotton Dress   
22    Short-sleeved Cotton Shirt   
23                  Jersey Dress   
24                      Leggings   
25           Cloud-shaped Mirror   
26      Short Puff-sleeved Dress   
27                   Derby Shoes   
28         Large Metal Plant Pot   
29            Graphic-detail Cap   
30                  5-pack Rings   
31     3-pack Short Boxer Shorts   
32            Relaxed-fit Hoodie   
33               Printed T-shirt   
34                  Denim Shorts   
35      Wrapover Cotton Bodysuit   
36                      Soft Toy   
37           5-pack Sports Socks   
38       Calf-length Satin Skirt   
39                 Smocked Dress   
40               Stoneware Plate   
41              Sweatshirt Dress   
42         2-pack Cotton Dresses   
43                Stoneware Bowl   
44           Quilted Laptop Case   
45   Ribbed Cashmere-blend Pants   
46                   Satin Shirt   
47                         Tunic   
48         Plumeti Chiffon Dress   
49                  Twill Shorts   

                                             Material  \
0   Details: Aluminum 100%Shell: Acrylonitrile-But...   
1                              Cotton 95%, Viscose 5%   
2                               Cotton 88%, Linen 12%   
3                          Polyester 98%, Elastane 2%   
4   Waist: Cotton 94%, Elastane 6%Coating: Polyure...   
5                Cotton 100%Cotton 60%, Polyester 40%   
6                                          Modal 100%   
7                             Cotton 95%, Elastane 5%   
8                                         Cotton 100%   
9                                 Steel 60%, Zinc 40%   
10  This product contains flammable substances and...   
11  Elastic ribbing: Cotton 97%, Elastane 3%Cotton...   
12                          Cotton 60%, Polyester 40%   
13  Hood lining: Polyester 100%Lining: Polyester 1...   
14                                        Cotton 100%   
15  Shell: Polyester 96%, Elastane 4%Lining: Polye...   
16                                     Polyester 100%   
17                         Polyester 77%, Viscose 23%   
18                                        Cotton 100%   
19  Lining: Polyester 100%Shell: Polyester 92%, El...   
20              Cotton 69%, Polyester 29%, Viscose 2%   
21                                        Cotton 100%   
22                                        Cotton 100%   
23                         Polyester 95%, Elastane 5%   
24                            Cotton 95%, Elastane 5%   
25  Main part: Medium Density Fiberboard 100%Frame...   
26                                             Fitted   
27  Lining and insole: Polyurethane 100%Sole: Ther...   
28                                         Metal 100%   
29                                     Polyester 100%   
30                                          Zinc 100%   
31                            Cotton 95%, Elastane 5%   
32                                        Relaxed fit   
33                                        Cotton 100%   
34             Cotton 82%, Polyester 17%, Elastane 1%   
35                                        Cotton 100%   
36   Cotton 65%, Polyester 35%Padding: Polyester 100%   
37  Cotton 75%, Polyamide